# Prepare Pollination syndrome data from TRY for use

The Pollination syndrome data from TRY informs on whether plants are pollinated by insects, animals,
wind, water or pollinate themselves.

*If you intend to clean more than one or two traits, we recommend the use
of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest
TRYSubset <- TRY[TraitName == "Pollination syndrome"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


There are some entries that need to be de-coded. This is true for entries with the value "yes" and numeric values.

In [ ]:
# decode coded entries
# yes
oriVals[oriVals == "yes"] <- TRYSubset[oriVals == "yes"]$OriglName
# numbers
oriVals[TRYSubset$DatasetID == 37 & oriVals == 0] <- "selfed"
oriVals[TRYSubset$DatasetID == 37 & oriVals == 1] <- "anemogamous"
oriVals[TRYSubset$DatasetID == 37 & oriVals %in% c(2, 3)] <- "zoophil"


It looks like a good idea to remove purely numeric values.

In [ ]:
oriVals[!grepl("[[:lower:]]", oriVals)] <- NA


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
# create a vector containing the search strings to look for to classify pollination into the following categories:
# pollination by "insects", "animals", "wind", "selfing", "water"
searchNames <- c(
	"entomo(ph|f)il|bugs|thysanoptera|homoptera|ants|insects?( always| \\(| the rule| pollinated| possible| often| rare|$)|entomogamous|bees?|hymenopter|flies|moths?|syrphid|wasp|dipteres|ichneumonidae", # nolint: line_length_linter.
	"zoophil|animals|bird|slug|Vertebrate|bio", # uppercase because from OriglName
	"anemo(ph|f)il|wind( always| the rule| possible| often| rare| pollinated|/|$)|anemogamous",
	"selfing the rule|selfed|autogamous|cleistogamy|geitonogamy|^self$|selfing( always| at failure of outcrossing| often| possible| rare)", # nolint: line_length_linter.
	"water( always| the rule| possible| often| rare| pollinated|$)|hydrogamous"
)


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like pollination categories
colnames(searchResults) <- c("entomophily", "zoophily", "anemophily", "self-pollination", "hydrophily")


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
oriVals[rowSums(searchResults) < 1]

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


We add a match with "zoophily" whenever we found "entomophily", as insects are animals.

In [ ]:
searchResults[searchResults[, 1] == TRUE, 2] <- TRUE # animals include category "insects"


Now, we can create new strings with the cleaned values and add them to the observations. To
not remove the original entries, we will create a new column called "CleanedValueStr".

In [ ]:
# use the searchResults matrix to create new value strings by concatenating all data found
newVals <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[searchResults[x, ]], collapse = ",")
})
newVals[newVals == ""] <- NA

# integrate into TRY
TRY[TraitName == "Pollination syndrome", CleanedValueStr := newVals]


Although not necessary, we may change the trait name.

In [ ]:
TRY[TraitName == "Pollination syndrome", TraitName := "Plant pollination syndrome"]


Let's write the data to a file.

In [ ]:
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
